# Identity Master List

- [x] MS Celeb 1M
- UMD Faces
- FaceScrub
- LFW
- PubFig
- PubFig83
- VGG Face
- VGG Face2
- IJB-C
- CASIA Webface
- IMDB-Face
- IMDB-Wiki

In [6]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob
from pathlib import Path
import requests
import json
from pprint import pprint
from multiprocessing.pool import ThreadPool
import threading
import urllib.request
import difflib
import unidecode

import slugify
from tqdm import tqdm_notebook as tqdm
import pandas as pd
from scipy.io import loadmat
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt

import sys
sys.path.append('/work/megapixels_dev/megapixels')
from app.utils import api_utils, identity_utils
from app.settings import app_cfg
from app.settings import types

## MS Celeb Top 1M

- add column for each spelling of name
- convert kg id to standard google format

In [7]:
fp_master_identities = '/data_store_hdd/apps/megapixels/metadata/identities_master_02.csv'
dir_msceleb_dloads = '/data_store_hdd/datasets/people/msceleb/downloads/'
fp_msceleb_clean_txt = join(dir_msceleb_dloads,'MS-Celeb-1M_clean_list.txt')

In [8]:
fp_msceleb_top1m = '/data_store_hdd/datasets/people/msceleb/downloads/Top1M_MidList.Name.tsv'
df_msceleb_top1m = pd.read_csv(fp_msceleb_top1m, delimiter='\t', header=None, encoding='utf-8', names=['id_kg', 'name_lang'])
df_msceleb_top1m_groups = df_msceleb_top1m.groupby('id_kg')
n_groups = df_msceleb_top1m_groups.ngroups

In [38]:
# create alphabetically sorted dict
msceleb_top1m_az = {}
for msceleb_row in tqdm(df_msceleb_top1m.itertuples(), total=len(df_msceleb_top1m)):
  name_lang = split_name_lang(msceleb_row.name_lang)
  name = name_lang['name']
  c = name[0].lower()
  if not c in msceleb_top1m_az.keys():
    msceleb_top1m_az[c] = []
  msceleb_top1m_az[c].append({'name': name, 'id_kg': msceleb_row.id_kg})

In [39]:
df_msceleb_top1m.head()

id_kg            name_lang
0  m.01008l47   Patrick Cummins@en
1  m.01008l47   Patrick Cummins@pt
2  m.01008l96  Mohamed Guessous@en
3  m.01008l96  Mohamed Guessous@fr
4  m.01008l96         محمد جسوس@ar

In [40]:
print(f'There are {len(df_msceleb_top1m):,} total name variations')
print(f'There are {n_groups:,} unique identities')

There are 3,481,186 total name variations
There are 1,000,000 unique identities


In [12]:
# convert DataFrame to dict
mseleb_top1m_records = df_msceleb_top1m.to_dict('records')

In [13]:
# store all identity info here, until creating dataframe
msceleb_identities = {}

In [14]:
# utility functions
def split_name_lang(name_lang):
  '''Split name into name and language'''
  if '@' in name_lang:
    indexes = [i for i,x in enumerate(name_lang) if x == '@']
    idx_max = (max(indexes))
    lang = name_lang[(idx_max + 1):]
    name = name_lang[:(idx_max)]
  else:
    name = name_lang
    lang = ''
  return {'name': name, 'lang': lang}

# temp save DataFrame to CSV
def save_identity_master(identities, fp_out=fp_master_identities):
  df_identities_master = pd.DataFrame.from_dict(identities)
  df_identities_master.index.name = 'id'
  df_identities_master.to_csv(fp_master_identities)

In [15]:
# convert to "name@lang" to dict format
msceleb_identities = {}
for mseleb_top1m_record in tqdm(mseleb_top1m_records):
  id_kg = mseleb_top1m_record['id_kg'].replace('m.','/m/')
  if not id_kg in msceleb_identities.keys():
    msceleb_identities[id_kg] = {'names': {}}
  name_lang = split_name_lang(mseleb_top1m_record['name_lang'])
  name = name_lang['name']
  lang = name_lang['lang']
  if lang == 'en':
      msceleb_identities[id_kg]['names']['canonical'] = name
  msceleb_identities[id_kg]['names'][lang] = name

### Patch @en names

In [16]:
# check for missing english names
for id_kg, attrs in tqdm(msceleb_identities.items()):
  lang_attrs = attrs['names']
  name_en = lang_attrs.get('en', None)
  if not name_en:
    print(f'no english name for {id_kg}')

no english name for /m/017vbn
no english name for /m/026q0k_
no english name for /m/02k2kw
no english name for /m/0bwhrg1



In [17]:
# patch en name exception: 4 names missing english
en_exceptions = {
  '/m/017vbn': 'de',
  '/m/026q0k_': 'nl',
  '/m/02k2kw': 'de',
  '/m/0bwhrg1': 'it'
}
for id_kg, lang in en_exceptions.items():
  msceleb_identities[id_kg]['names']['en'] = msceleb_identities[id_kg]['names'][lang]
  msceleb_identities[id_kg]['names']['canonical'] = msceleb_identities[id_kg]['names']['en']
  print(f'patched {id_kg} {lang} to en')

patched /m/017vbn de to en
patched /m/026q0k_ nl to en
patched /m/02k2kw de to en
patched /m/0bwhrg1 it to en


### Remove duplicate names

In [18]:
# de-duplicate names that use same spelling for multiple languages
items_removed = []
msceleb_identities_copy = msceleb_identities.copy()

for id_kg, attrs in tqdm(msceleb_identities_copy.items()):
  lang_attrs = attrs['names']
  name_main = lang_attrs.get('canonical', None)
  if not name_en:
    print('error. all names need "en"')
    break
  lang_attrs_copy = attrs['names'].copy()
  for lang, name in lang_attrs_copy.items():
    if name == name_main and lang != 'en' and lang != 'canonical':
      # remove it
      items_removed.append(msceleb_identities[id_kg]['names'].pop(lang))
  del lang_attrs_copy

del msceleb_identities_copy
print(f'removed {len(items_removed):,} duplicate names')
del items_removed


removed 1,485,336 duplicate names


### Count images per person for ms celeb

In [19]:
# calculate total images per id
msceleb_files = {}
# load text file
with open(fp_msceleb_clean_txt,'r') as fp:
  msceleb_lines = fp.readlines()
  
# iterate lines and append all files
for filepath in tqdm(msceleb_lines):
  id_kg, fname = filepath.split('/')
  id_kg = id_kg.replace('m.', '/m/')
  if not id_kg in msceleb_files.keys():
    msceleb_files[id_kg] = []
  msceleb_files[id_kg].append(fname)

In [20]:
# add count to 
for id_kg, attrs in tqdm(msceleb_identities.items()):
  if id_kg in msceleb_files.keys():
    count = len(msceleb_files[id_kg])
  else:
    count = 0
  msceleb_identities[id_kg]['count_msceleb'] = count

In [21]:
im_counts_idxs = [attrs['count_msceleb'] for id_kg, attrs in msceleb_identities.items()]
im_counts_id_kg = [id_kg for id_kg, _ in msceleb_identities.items()]

In [22]:
# print stats
idx_max = np.argmax(im_counts_idxs)
id_kg_max = im_counts_id_kg[idx_max]
count_max = im_counts_idxs[idx_max]
name_max = msceleb_identities[id_kg_max]['names']['canonical']
print(f'Most images {count_max:,} for {name_max}')
# distribution
im_counts_idxs = np.array(im_counts_idxs)
print(f'{len(im_counts_idxs[im_counts_idxs > 10]):,} more than 10')
print(f'{len(im_counts_idxs[im_counts_idxs > 20]):,} more than 20')
print(f'{len(im_counts_idxs[im_counts_idxs > 50]):,} more than 50')
print(f'{len(im_counts_idxs[im_counts_idxs > 100]):,} more than 100')

Most images 130 for Leelee Sobieski
88,244 more than 10
78,027 more than 20
49,042 more than 50
5,025 more than 100


In [23]:
# awkward conversion of msceleb_identities to a list of dicts
identities_flat = []
for id_kg, attrs in tqdm(msceleb_identities.items()):
  obj = {'id_kg': id_kg}
  for lang, name in attrs['names'].items():
    if lang != 'canonical':
        col_name = f'name_msceleb_{lang}'
    elif lang == 'canonical':
      col_name = 'name_msceleb'
    obj[col_name] = name
  obj['count_msceleb'] = attrs['count_msceleb']
  identities_flat.append(obj)

In [24]:
# convert to dataframe
df_identities = pd.DataFrame.from_dict(identities_flat)

In [25]:
# save checkpoint CSV
save_identity_master(identities_flat)  # encoding='utf-16' ??

In [26]:
# copy to master and delete ref to msceleb
identities = msceleb_identities.copy()
del msceleb_identities

## LFW

In [28]:
# add LFW data
fp_lfw = '/data_store_hdd/datasets/people/lfw/downloads/lfw-names.txt'
with open(fp_lfw,'r') as fp:
  lfw_lines = fp.readlines()
lfw_lines = [x.strip() for x in lfw_lines]

lfw_meta = []
for lfw_line in lfw_lines:
  name_orig, count = lfw_line.split('\t')
  name_clean = name_orig.replace('_',' ')
  obj = {'name_orig': name_orig, 'name': name_clean, 'count':count}
  lfw_meta.append(obj)

In [29]:
identities_tmp = identities.copy()

In [46]:
# make exact name matches
lfw_name_matches_exact = {}
for lfw_item in tqdm(lfw_meta):
  lfw_name = lfw_item['name']  # name is transformed original name
  lfwnl = lfw_name.lower()
  c = lfwnl[0]
  for name_id_kg in msceleb_top1m_az[c]:
    name = name_id_kg['name']
    id_kg = name_id_kg['id_kg']
    if lfwnl == name.lower():
      lfw_name_matches_exact[lfw_name] = id_kg
      print(f"matched: {lfw_name} to {name} with id: {id_kg}")
      break

matched: Aaron Eckhart to Aaron Eckhart with id: m.03t4cz
matched: Aaron Guiel to Aaron Guiel with id: m.0bsy4r
matched: Aaron Peirsol to Aaron Peirsol with id: m.03p4zn
matched: Aaron Sorkin to Aaron Sorkin with id: m.01d8yn
matched: Aaron Tippin to Aaron Tippin with id: m.01k8mzv
matched: Abba Eban to Abba Eban with id: m.01341q
matched: Abbas Kiarostami to Abbas Kiarostami with id: m.023t0q
matched: Abdoulaye Wade to Abdoulaye Wade with id: m.023066
matched: Abdul Rahman to Abdul Rahman with id: m.01_t7m
matched: Abdullah to Abdullah with id: m.081x04
matched: Abdullah Ahmad Badawi to Abdullah Ahmad Badawi with id: m.01yynm
matched: Abel Aguilar to Abel Aguilar with id: m.08q415
matched: Abel Pacheco to Abel Pacheco with id: m.022vvl
matched: Abid Hamid Mahmud Al-Tikriti to Abid Hamid Mahmud al-Tikriti with id: m.03h33y
matched: Abraham Foxman to Abraham Foxman with id: m.03rtwj
matched: Adam Ant to Adam Ant with id: m.01wgjj5
matched: Adam Freier to Adam Freier with id: m.0f3mns
ma

matched: Ana Palacio to Ana Palacio with id: m.0606x3
matched: Anastasia Kelesidou to Anastasia Kelesidou with id: m.07ztqs
matched: Anastasia Myskina to Anastasia Myskina with id: m.031h9y
matched: Anatoliy Kinakh to Anatoliy Kinakh with id: m.04hl61
matched: Anders Fogh Rasmussen to Anders Fogh Rasmussen with id: m.01p9wn
matched: Andre Agassi to Andre Agassi with id: m.0hdr
matched: Andre Lange to Andre Lange with id: m.0bsp5t
matched: Andrea Bocelli to Andrea Bocelli with id: m.02b25y
matched: Andrea De Cruz to Andrea De Cruz with id: m.0j7z2dh
matched: Andrea Yates to Andrea Yates with id: m.01tr5l
matched: Andreas Vinciguerra to Andreas Vinciguerra with id: m.0bdr9r
matched: Andrei Konchalovsky to Andrei Konchalovsky with id: m.03lhhq
matched: Andrei Mikhnevich to Andrei Mikhnevich with id: m.09dlrc
matched: Andrei Nikolishin to Andrei Nikolishin with id: m.0927tv
matched: Andrew Bernard to Andrew Bernard with id: m.02r6722
matched: Andrew Caldecott to Andrew Caldecott with id: m

matched: Bernardo Segura to Bernardo Segura with id: m.0bnr7m
matched: Bertie Ahern to Bertie Ahern with id: m.09_9nl
matched: Bertrand Bonello to Bertrand Bonello with id: m.02rzksd
matched: Beth Jones to Beth Jones with id: m.05v_jh0
matched: Bettina Rheims to Bettina Rheims with id: m.03pfyf
matched: Betty Williams to Betty Williams with id: m.02848d
matched: Bianca Jagger to Bianca Jagger with id: m.04l_7q
matched: Bijan Namdar Zangeneh to Bijan Namdar Zangeneh with id: m.07wh4x
matched: Bill Belichick to Bill Belichick with id: m.02_fs7
matched: Bill Butler to Bill Butler with id: m.025v92r
matched: Bill Callahan to Bill Callahan with id: m.05v5sz
matched: Bill Cartwright to Bill Cartwright with id: m.05zr5r1
matched: Bill Clancy to Bill Clancy with id: m.0fqq2b9
matched: Bill Clinton to Bill Clinton with id: m.0157m
matched: Bill Curry to Bill Curry with id: m.09zdxg
matched: Bill Doba to Bill Doba with id: m.07jd41
matched: Bill Elliott to Bill Elliott with id: m.04dzh1r
matched

matched: Candice Bergen to Candice Bergen with id: m.04p_yxz
matched: Candie Kung to Candie Kung with id: m.075hcr
matched: Carey Lowell to Carey Lowell with id: m.041l94
matched: Carin Koch to Carin Koch with id: m.0djjc7
matched: Carl Levin to Carl Levin with id: m.01xh6j
matched: Carl Pope to Carl Pope with id: m.0dnqf0
matched: Carl Reiner to Carl Reiner with id: m.0pnf3
matched: Carla Del Ponte to Carla Del Ponte with id: m.04y3tl
matched: Carla Gay Balingit to Carla Gay Balingit with id: m.0bz3cc
matched: Carla Gugino to Carla Gugino with id: m.06qgvf
matched: Carla Moreno to Carla Moreno with id: m.05tg6p
matched: Carla Sullivan to Carla Sullivan with id: m.0h7mj1v
matched: Carlo Ancelotti to Carlo Ancelotti with id: m.049_yr
matched: Carlo Azeglio Ciampi to Carlo Azeglio Ciampi with id: m.01l__3
matched: Carlos Alberto Parreira to Carlos Alberto Parreira with id: m.037n_q
matched: Carlos Arroyo to Carlos Arroyo with id: m.076x8t8
matched: Carlos Barra to Carlos Barra with id: m

matched: Cindy Klassen to Cindy Klassen with id: m.08z9xg
matched: Cindy Margolis to Cindy Margolis with id: m.05vxct
matched: Cindy Taylor to Cindy Taylor with id: m.07dn76
matched: Ciro Gomes to Ciro Gomes with id: m.0b4fnb
matched: Claire Danes to Claire Danes with id: m.01gq0b
matched: Claire Tomalin to Claire Tomalin with id: m.0253pn
matched: Clare Short to Clare Short with id: m.01bl0h
matched: Claude Jorda to Claude Jorda with id: m.0gjcvjj
matched: Claudia Cardinale to Claudia Cardinale with id: m.01j5sv
matched: Claudia Coslovich to Claudia Coslovich with id: m.0269h89
matched: Claudia Pechstein to Claudia Pechstein with id: m.07hxkb
matched: Claudia Schiffer to Claudia Schiffer with id: m.0m2wm
matched: Claudine Farrell to Claudine Farrell with id: m.0b67b9d
matched: Claudio Abbado to Claudio Abbado with id: m.01l9pz
matched: Claudio Ranieri to Claudio Ranieri with id: m.02_jy3
matched: Clay Aiken to Clay Aiken with id: m.01y3qy
matched: Cliff Ellis to Cliff Ellis with id: m

...

matched: Ray Bradbury to Ray Bradbury with id: m.06jcc
matched: Ray Evernham to Ray Evernham with id: m.06_74n
matched: Ray Halbritter to Ray Halbritter with id: m.047mjzp
matched: Ray Liotta to Ray Liotta with id: m.02j490
matched: Ray Lucas to Ray Lucas with id: m.03ydd_3
matched: Ray Nagin to Ray Nagin with id: m.06jp4q
matched: Ray Price to Ray Price with id: m.0hzqg_d
matched: Ray Romano to Ray Romano with id: m.01h910
matched: Ray Sherman to Ray Sherman with id: m.05mznbs
matched: Ray Young to Ray Young with id: m.05mxz8z
matched: Raymond Odierno to Raymond Odierno with id: m.0268g3w
matched: Raza Rabbani to Raza Rabbani with id: m.03yj5dv
matched: Razali Ismail to Razali Ismail with id: m.044x82
matched: Red Auerbach to Red Auerbach with id: m.01t2df
matched: Reese Witherspoon to Reese Witherspoon with id: m.0n6f8
matched: Reggie Lewis to Reggie Lewis with id: m.03hk1tz
matched: Reggie Miller to Reggie Miller with id: m.02c5ls
matched: Reggie Sanders to Reggie Sanders with id: m

matched: Rohinton Mistry to Rohinton Mistry with id: m.0gr21
matched: Roland Koch to Roland Koch with id: m.0404bdc
matched: Rolandas Paksas to Rolandas Paksas with id: m.01xvhg
matched: Rolf Eckrodt to Rolf Eckrodt with id: m.0gjs5y
matched: Rollie Massimino to Rollie Massimino with id: m.05k185
matched: Romain Duris to Romain Duris with id: m.0615j_
matched: Roman Abramovich to Roman Abramovich with id: m.01zl71
matched: Roman Coppola to Roman Coppola with id: m.074tyf
matched: Roman Polanski to Roman Polanski with id: m.06b_0
matched: Roman Tam to Roman Tam with id: m.0vgmx
matched: Romano Prodi to Romano Prodi with id: m.01c3z5
matched: Romeo Gigli to Romeo Gigli with id: m.0dsbldr
matched: Ron Dittemore to Ron Dittemore with id: m.01jh6j
matched: Ron Gonzales to Ron Gonzales with id: m.05fvnl
matched: Ron Howard to Ron Howard with id: m.0g2lq
matched: Ron Kirk to Ron Kirk with id: m.02fhhn
matched: Ron Zook to Ron Zook with id: m.07072y
matched: Ronald Harwood to Ronald Harwood wi

matched: Sheila Taormina to Sheila Taormina with id: m.05tf7q
matched: Sheila Wellstone to Sheila Wellstone with id: m.04gkt6
matched: Sheldon Silver to Sheldon Silver with id: m.06dn4y
matched: Sherri Coale to Sherri Coale with id: m.0d5bxd
matched: Sheryl Crow to Sheryl Crow with id: m.06rgq
matched: Shi Guangsheng to Shi Guangsheng with id: m.04lf22t
matched: Shia LaBeouf to Shia LaBeouf with id: m.04w391
matched: Shigeo Nagashima to Shigeo Nagashima with id: m.01zv51
matched: Shigeru Ishiba to Shigeru Ishiba with id: m.03f5mf
matched: Shimon Peres to Shimon Peres with id: m.0c_8s
matched: Shingo Katayama to Shingo Katayama with id: m.06nxp4
matched: Shingo Suetsugu to Shingo Suetsugu with id: m.046x06
matched: Shinya Taniguchi to Shinya Taniguchi with id: m.0j_4brn
matched: Shinzo Abe to Shinzo Abe with id: m.07t7hy
matched: Shobha De to Shobha De with id: m.05hsn2
matched: Shoshana Johnson to Shoshana Johnson with id: m.05nltd
matched: Shoshannah Stern to Shoshannah Stern with id:

matched: Tang Jiaxuan to Tang Jiaxuan with id: m.05df3p
matched: Tara Kirk to Tara Kirk with id: m.0fvffw
matched: Tara Reid to Tara Reid with id: m.032wdd
matched: Tara VanDerveer to Tara VanDerveer with id: m.08q7kb
matched: Tassos Papadopoulos to Tassos Papadopoulos with id: m.022dpx
matched: Tatiana Panova to Tatiana Panova with id: m.02ryjj_
matched: Tatiana Shchegoleva to Tatiana Shchegoleva with id: m.04jbc_k
matched: Tatsuya Fuji to Tatsuya Fuji with id: m.05zlbz8
matched: Tatyana Tomashova to Tatyana Tomashova with id: m.09j36c
matched: Taufik Hidayat to Taufik Hidayat with id: m.03nrss
matched: Taylor Twellman to Taylor Twellman with id: m.03zyxy
matched: Tayshaun Prince to Tayshaun Prince with id: m.03qdw5
matched: Ted Christopher to Ted Christopher with id: m.03mdpqd
matched: Ted Maher to Ted Maher with id: m.04zzv3c
matched: Ted Nolan to Ted Nolan with id: m.02yjf8
matched: Ted Turner to Ted Turner with id: m.07hkd
matched: Ted Washington to Ted Washington with id: m.05ymz

matched: Trista Rehn to Trista Rehn with id: m.05dcbl
matched: Tristan Gretzky to Tristan Gretzky with id: m.0j2h3yn
matched: Troy Aikman to Troy Aikman with id: m.0dr5g9
matched: Troy Garity to Troy Garity with id: m.06zttt
matched: Troy Polamalu to Troy Polamalu with id: m.04m0nc
matched: Trudi Lacey to Trudi Lacey with id: m.0ds8xbl
matched: Tsutomu Takebe to Tsutomu Takebe with id: m.07w76b
matched: Tubby Smith to Tubby Smith with id: m.05hkc6
matched: Tung Chee-hwa to Tung Chee-Hwa with id: m.0mbs_
matched: Turner Gill to Turner Gill with id: m.08pg9y
matched: Turner Stevenson to Turner Stevenson with id: m.09xvn5
matched: Ty Votaw to Ty Votaw with id: m.0brtq2
matched: Tyler Hamilton to Tyler Hamilton with id: m.0fvcsw
matched: Tyra Banks to Tyra Banks with id: m.01jbx1
matched: Tzipora Obziler to Tzipora Obziler with id: m.08w04b
matched: Uday Hussein to Uday Hussein with id: m.01c3y8
matched: Uma Thurman to Uma Thurman with id: m.0kjrx
matched: Urmila Matondkar to Urmila Matond

In [51]:
print(f'found {len(lfw_name_matches_exact)} of {len(lfw_meta)} names using exact matches')

found 3616 of 5749 names using exact matches


In [56]:
'Adrien Brody' in lfw_name_matches_exact.keys()

True

In [64]:
# make sanitized
lfw_name_matches_clean = {}
for lfw_item in tqdm(lfw_meta):
  lfw_name = lfw_item['name']  # name is transformed original name
  if lfw_name not in lfw_name_matches_exact.keys():
    print(f'clean matching: {lfw_name} ...')
    matched_id_kg = None
    for id_kg, identity in identities_tmp.items():
      # for each msceleb identity, look for match
      for lang, name in identity['names'].items():
        # for each name's language variation, look for match
        strict_match = identity_utils.names_match_strict(lfw_name, name)
        if strict_match:
          matched_id_kg = id_kg
          matched_lang = lang
          matched_name = name
          break
      if matched_id_kg:
        print(f'matched {lfw_name} to {matched_name} in {matched_lang}. Add to matched ids')
        lfw_name_matches_clean[lfw_name] = matched_id_kg
        break
    if not matched_id_kg:
      print(f'could not find: {lfw_name}')
print(f'found {len(lfw_name_matches_clean)} of {len(lfw_meta)} names using exact matches')

clean matching: AJ Cook ...
matched AJ Cook to A. J. Cook in canonical. Add to matched ids
clean matching: AJ Lamas ...
matched AJ Lamas to A.J. Lamas in canonical. Add to matched ids
clean matching: Aaron Patterson ...
could not find: Aaron Patterson
clean matching: Aaron Pena ...
matched Aaron Pena to Aaron Peña in canonical. Add to matched ids
clean matching: Abdel Aziz Al-Hakim ...
could not find: Abdel Aziz Al-Hakim
clean matching: Abdel Madi Shabneh ...
could not find: Abdel Madi Shabneh
clean matching: Abdel Nasser Assidi ...
could not find: Abdel Nasser Assidi
clean matching: Abdul Majeed Shobokshi ...
could not find: Abdul Majeed Shobokshi
clean matching: Abdulaziz Kamilov ...
matched Abdulaziz Kamilov to Abdulaziz Komilov in canonical. Add to matched ids
clean matching: Abdullah Nasseef ...
could not find: Abdullah Nasseef
clean matching: Abdullah al-Attiyah ...
could not find: Abdullah al-Attiyah
clean matching: Abdullatif Sener ...
could not find: Abdullatif Sener
clean mat

could not find: Andy Perez
clean matching: Andy Wisecarver ...
could not find: Andy Wisecarver
clean matching: Anette Hosoi ...
could not find: Anette Hosoi
clean matching: Angel Lockward ...
could not find: Angel Lockward
clean matching: Angel Maza ...
could not find: Angel Maza
clean matching: Angela Alvarado Rosa ...
could not find: Angela Alvarado Rosa
clean matching: Angela Mascia-Frye ...
could not find: Angela Mascia-Frye
clean matching: Angelica Romero ...
could not find: Angelica Romero
clean matching: Angelo Genova ...
could not find: Angelo Genova
clean matching: Angelo Reyes ...
could not find: Angelo Reyes
clean matching: Angie Arzola ...
could not find: Angie Arzola
clean matching: Anibal Ibarra ...
could not find: Anibal Ibarra
clean matching: Anil Ramsook ...
could not find: Anil Ramsook
clean matching: Anja Paerson ...
could not find: Anja Paerson
clean matching: Anjum Hussain ...
could not find: Anjum Hussain
clean matching: Ann Godbehere ...
could not find: Ann Godbe

could not find: Billy Rork
clean matching: Billy Sollie ...
could not find: Billy Sollie
clean matching: Billy Tibbets ...
could not find: Billy Tibbets
clean matching: Bob Cantrell ...
could not find: Bob Cantrell
clean matching: Bob Colvin ...
could not find: Bob Colvin
clean matching: Bob Crippen ...
could not find: Bob Crippen
clean matching: Bob Curtis ...
could not find: Bob Curtis
clean matching: Bob Eskridge ...
could not find: Bob Eskridge
clean matching: Bob Goldman ...
could not find: Bob Goldman
clean matching: Bob Hartley ...
could not find: Bob Hartley
clean matching: Bob Herz ...
could not find: Bob Herz
clean matching: Bob Melvin ...
could not find: Bob Melvin
clean matching: Bob Petrino ...
matched Bob Petrino to Bob Petrie in canonical. Add to matched ids
clean matching: Bob Riley ...
could not find: Bob Riley
clean matching: Bob Sulkin ...
could not find: Bob Sulkin
clean matching: Bob Wright ...
could not find: Bob Wright
clean matching: Bobby Goldwater ...
could no

could not find: Charles Holzner
clean matching: Charles Ingram ...
could not find: Charles Ingram
clean matching: Charles Kartman ...
matched Charles Kartman to Chester Kallman in canonical. Add to matched ids
clean matching: Charles Lebois ...
could not find: Charles Lebois
clean matching: Charles Mathews ...
matched Charles Mathews to Matthew Charles in canonical. Add to matched ids
clean matching: Charles Pickering ...
could not find: Charles Pickering
clean matching: Charles Pouty ...
could not find: Charles Pouty
clean matching: Charles Tannok ...
could not find: Charles Tannok
clean matching: Charley Armey ...
matched Charley Armey to Aryeh Carmell in canonical. Add to matched ids
clean matching: Charlie Deane ...
matched Charlie Deane to Charlie Deal in canonical. Add to matched ids
clean matching: Charlotte Chambers ...
could not find: Charlotte Chambers
clean matching: Chawki Armali ...
could not find: Chawki Armali
clean matching: Chea Sophara ...
matched Chea Sophara to Sara

could not find: Daniela Hantuchova
clean matching: Daniele Bergamin ...
could not find: Daniele Bergamin
clean matching: Daniele Hypolito ...
could not find: Daniele Hypolito
clean matching: Daniell Sunjata ...
could not find: Daniell Sunjata
clean matching: Danis Tanovic ...
could not find: Danis Tanovic
clean matching: Danny Avalon ...
could not find: Danny Avalon
clean matching: Danny Morgan ...
could not find: Danny Morgan
clean matching: Dario Camuffo ...
could not find: Dario Camuffo
clean matching: Darko Milicic ...
could not find: Darko Milicic
clean matching: Darlene Garrettson ...
could not find: Darlene Garrettson
clean matching: Darren Campel ...
could not find: Darren Campel
clean matching: Daryl Parks ...
could not find: Daryl Parks
clean matching: Dave Johnson ...
could not find: Dave Johnson
clean matching: Dave Lewis ...
could not find: Dave Lewis
clean matching: Dave McNealey ...
could not find: Dave McNealey
clean matching: Dave Potter ...
matched Dave Potter to Dave

...

could not find: Odilia Collazo
clean matching: Olesya Bonabarenko ...
could not find: Olesya Bonabarenko
clean matching: Oliver Phelps ...
could not find: Oliver Phelps
clean matching: Olivera Labus ...
could not find: Olivera Labus
clean matching: Omar Khan Sharif ...
could not find: Omar Khan Sharif
clean matching: Omar el-Heib ...
could not find: Omar el-Heib
clean matching: Ontario Lett ...
could not find: Ontario Lett
clean matching: Oracene Williams ...
could not find: Oracene Williams
clean matching: Osama Al Baz ...
could not find: Osama Al Baz
clean matching: Oscar Bolanos ...
could not find: Oscar Bolanos
clean matching: Oscar DLeon ...
could not find: Oscar DLeon
clean matching: Oscar Elias Biscet ...
could not find: Oscar Elias Biscet
clean matching: Osmond Smith ...
could not find: Osmond Smith
clean matching: Osrat Iosef ...
could not find: Osrat Iosef
clean matching: Oswald Gruebel ...
could not find: Oswald Gruebel
clean matching: Oswaldo Paya ...
could not find: Oswald

could not find: Raaf Schefter
clean matching: Raag Singhal ...
could not find: Raag Singhal
clean matching: Rachel Leigh Cook ...
could not find: Rachel Leigh Cook
clean matching: Rachel Wadsworth ...
could not find: Rachel Wadsworth
clean matching: Rachel Wheatley ...
could not find: Rachel Wheatley
clean matching: Radovan Karadzic ...
could not find: Radovan Karadzic
clean matching: Rafael Ramirez ...
could not find: Rafael Ramirez
clean matching: Rafael Vinoly ...
matched Rafael Vinoly to Rafael Viñoly in canonical. Add to matched ids
clean matching: Raghad Saddam Hussein ...
could not find: Raghad Saddam Hussein
clean matching: Rainer Geulen ...
could not find: Rainer Geulen
clean matching: Rainer Gut ...
could not find: Rainer Gut
clean matching: Rainer Schuettler ...
could not find: Rainer Schuettler
clean matching: Raja Ibrahim ...
could not find: Raja Ibrahim
clean matching: Raja Qureshi ...
could not find: Raja Qureshi
clean matching: Raja Ramani ...
could not find: Raja Raman

could not find: Ronaldo Luis Nazario de Lima
clean matching: Rosa Haywa de Condori ...
could not find: Rosa Haywa de Condori
clean matching: Rosalie Perkov ...
could not find: Rosalie Perkov
clean matching: Rosalyn Carter ...
matched Rosalyn Carter to Rosalynn Carter in canonical. Add to matched ids
clean matching: Rose Linkins ...
matched Rose Linkins to Rose Likins in it. Add to matched ids
clean matching: Rosny Desroches ...
could not find: Rosny Desroches
clean matching: Roy Moore ...
could not find: Roy Moore
clean matching: Ruano Pascual ...
could not find: Ruano Pascual
clean matching: Ruben Sierra ...
could not find: Ruben Sierra
clean matching: Ruben Wolkowyski ...
could not find: Ruben Wolkowyski
clean matching: Rubens Barrichello ...
could not find: Rubens Barrichello
clean matching: Rudi Voeller ...
could not find: Rudi Voeller
clean matching: Rudolph Holton ...
could not find: Rudolph Holton
clean matching: Rustu Recber ...
could not find: Rustu Recber
clean matching: Ruth

could not find: Stephen Ebberharter
clean matching: Stephen Glassroth ...
could not find: Stephen Glassroth
clean matching: Stephen Keener ...
could not find: Stephen Keener
clean matching: Stephen Oake ...
could not find: Stephen Oake
clean matching: Stephen Push ...
could not find: Stephen Push
clean matching: Stephen Swindal ...
could not find: Stephen Swindal
clean matching: Steve Allan ...
could not find: Steve Allan
clean matching: Steve Blankenship ...
could not find: Steve Blankenship
clean matching: Steve Coterill ...
could not find: Steve Coterill
clean matching: Steve Fehr ...
could not find: Steve Fehr
clean matching: Steve Lenard ...
could not find: Steve Lenard
clean matching: Steve Nash ...
could not find: Steve Nash
clean matching: Steve Nesbitt ...
matched Steve Nesbitt to Steve Nisbett in canonical. Add to matched ids
clean matching: Steve Pagliuca ...
could not find: Steve Pagliuca
clean matching: Steve Patterson ...
matched Steve Patterson to Steven Patterson in can

could not find: Tommy Tubberville
clean matching: Tono Suratman ...
could not find: Tono Suratman
clean matching: Tony Bennett ...
could not find: Tony Bennett
clean matching: Tony Cummo ...
could not find: Tony Cummo
clean matching: Tony LaRussa ...
matched Tony LaRussa to Tony La Russa in canonical. Add to matched ids
clean matching: Tonya Payne ...
could not find: Tonya Payne
clean matching: Tora Takagi ...
could not find: Tora Takagi
clean matching: Toshi Izawa ...
could not find: Toshi Izawa
clean matching: Tracee Treadwell ...
could not find: Tracee Treadwell
clean matching: Tracy Wyle ...
could not find: Tracy Wyle
clean matching: Travis Rudolph ...
could not find: Travis Rudolph
clean matching: Trevor Watson ...
matched Trevor Watson to Trevor Watts in canonical. Add to matched ids
clean matching: Trisha Meili ...
could not find: Trisha Meili
clean matching: Troy Hudson ...
could not find: Troy Hudson
clean matching: Troy Jenkins ...
could not find: Troy Jenkins
clean matching:

In [141]:
# compare this this to master identity
for lfw_item in tqdm(lfw_meta, desc='1st loop'):
    
  # for each LFW name, look for match
  lfw_name = lfw_item['name']
  matched_id = None
  
  for id_kg, identity in identities_tmp.items():
    # for each msceleb identity, look for match
    for lang, name in identity['names'].items():
      # for each name's language variation, look for match
      if not len(name) > 0:
        print('no name')
        continue
      strict_match = identity_utils.names_match_strict(lfw_name, name)
      if strict_match:
        #print(f'Strict matched "{lfw_name}" to "{name}"')
        matched_id = id_kg
        matched_lang = lang
        matched_name = name
        break
    if matched_id:
      matched_lang = lang
      matched_name = name
      print(f'OK. Found match: {lfw_name} == {matched_name} in lang: {matched_lang}')
      pbar_ids.clear()
      pbar_ids.close()
      break
  if not matched_id:
    print(f'ERROR: could not find {lfw_name}')
      

Found: Aaron Eckhart@ca
Found: Aaron Guiel@en
Found: Aaron Peirsol@ca
Found: Aaron Sorkin@ca
Found: Aaron Tippin@de
Found: Abba Eban@cs
Found: Abbas Kiarostami@ca
Found: Abdoulaye Wade@ca
Found: Abdul Rahman Lestaluhu@id
Found: Abdullah Cabir@tr
Found: Abdullah Ahmad Badawi@da
Found: Abdullah Gulam Rasoul@en
Found: Abel Aguilar@cs
Found: Abel Pacheco de la Espriella@es
Found: Abid Hamid Mahmud al-Tikriti@nl
Found: Abraham Foxman@cs
Found: Adam Ant@cs
Found: Adam Freier@en
Found: Adam Herbert@en
Found: Adam Mair@de
Found: Adam Richards@en
Found: Adam Sandler@ca
Found: George Adam Scott@en
Found: Adel Al-Jubeir@fr
Found: Adolfo Rodriguez Saa@id
Found: Adrian McPherson@en
Found: Adrian Murrell@en
Found: Adriana Lima@ca
Found: Adrien Brody@ca
Found: Afton Smith@cs
Found: Agbani Darego@de
Found: Agnelo Queiroz@en
Found: Agnes Bruckner@de
Found: Ahmed Ahmedou@de
Found: Ahmed Chalabi@en
Found: Mahmood Ahmed Ghazi@en
Found: Ahmet Necdet Sezer@ca
Found: Ai Sugiyama@da
Found: Aidan Quinn@ca
Foun

Found: Bill Callahan@en
Found: Bill Cartwright@en
Found: Bill Clancy@en
Found: Bill Clinton@ca
Found: Bill Curry@en
Found: Bill Doba@en
Found: Bill Elliott@pt
Found: Bill Fennelly@en
Found: Bill Frist@de
Found: Bill Gates@ca
Found: Bill Grahame@en
Found: Bill Guerin@de
Found: Bill Herrion@en
Found: Bill Hughes@en
Found: Bill Kollar@en
Found: Bill Kong@es
Found: Bill Mauldin@de
Found: Bill McBride@en
Found: Bill Nelson@da
Found: Bill Parcells@de
Found: Bill Parsons@en
Found: Bill Paxton@ca
Found: Bill Self@de
Found: Bill Sizemore@en
Found: Bill Stapleton@en
Found: Bill Steinke@en
Found: Bill Walton@de
Found: Billy Andrade@da
Found: Billy Beane@de
Found: Billy Bob Thornton@ca
Found: Billy Boyd@en
Found: Billy Crawford@de
Found: Billy Crystal@ca
Found: Billy Donovan@en
Found: Billy Gilman@en
Found: Billy Joel@ca
Found: Bing Crosby@ca
Found: Binyamin Ben-Eliezer@en
Found: Bison Dele@de
Found: Bixente Lizarazu@ca
Found: Blas Ople@de
Found: Blythe Danner@ca
Found: Blythe Hartley@de
Found: Bo

KeyboardInterrupt: 

In [103]:
identity_utils.names_match_strict('AJ Cook', 'A.J. Cook')

True

In [105]:
names_match('A.J. Cook', 'cook Aj', as_float=True, compound_score=True)

1.0

## PubFig

In [ ]:
# add pubfig data

## Face Scrub

In [ ]:
# add facescrub

## UMD Faces

In [ ]:
# add umd

## CASIA Webface

In [ ]:
# add CASIA Webface

# IMDB Wiki

In [ ]:
# add imdb-wiki

## IMDB-Face

In [ ]:
# add imdb face